<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Parse-Big-Spreadsheet" data-toc-modified-id="Parse-Big-Spreadsheet-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Parse Big Spreadsheet</a></span><ul class="toc-item"><li><span><a href="#Update-2018" data-toc-modified-id="Update-2018-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Update 2018</a></span><ul class="toc-item"><li><span><a href="#DBpedia" data-toc-modified-id="DBpedia-1.1.1"><span class="toc-item-num">1.1.1&nbsp;&nbsp;</span>DBpedia</a></span></li></ul></li><li><span><a href="#Pandas" data-toc-modified-id="Pandas-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Pandas</a></span><ul class="toc-item"><li><span><a href="#Steps" data-toc-modified-id="Steps-1.2.1"><span class="toc-item-num">1.2.1&nbsp;&nbsp;</span>Steps</a></span></li></ul></li></ul></li><li><span><a href="#Read-the-csv-file-in-chunks" data-toc-modified-id="Read-the-csv-file-in-chunks-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Read the csv file in chunks</a></span></li><li><span><a href="#Now-with-a-big-file" data-toc-modified-id="Now-with-a-big-file-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Now with a big file</a></span></li><li><span><a href="#Really-big-file" data-toc-modified-id="Really-big-file-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Really big file</a></span><ul class="toc-item"><li><span><a href="#Techniques" data-toc-modified-id="Techniques-4.1"><span class="toc-item-num">4.1&nbsp;&nbsp;</span>Techniques</a></span><ul class="toc-item"><li><span><a href="#Inspect-the-file" data-toc-modified-id="Inspect-the-file-4.1.1"><span class="toc-item-num">4.1.1&nbsp;&nbsp;</span>Inspect the file</a></span></li></ul></li></ul></li><li><span><a href="#Reading-a-gzipped-file-line-by-line" data-toc-modified-id="Reading-a-gzipped-file-line-by-line-5"><span class="toc-item-num">5&nbsp;&nbsp;</span><a>Reading a gzipped file line by line</a></a></span></li></ul></div>

# Parse Big Spreadsheet

## Update 2018
* The DBpedia files have moved to another location: see the [Readme](http://wiki.dbpedia.org/services-resources/downloads/dbpedia-tables). E.g., <http://web.informatik.uni-mannheim.de/DBpediaAsTables/csv/Band.csv.gz> is now avialable at <http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Band.csv.gz>


1. We use pandas
1. We take a DBpedia dump as an example: <http://web.informatik.uni-mannheim.de/DBpediaAsTables/csv/Band.csv.gz>


### DBpedia
* Information on their downloads as csv <https://github.com/dbpedia/dbpedia/tree/master/tools/DBpediaAsTables> 
* Downloads:  For each class a separate json/csv file <http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/DBpediaClasses.htm>

## Pandas

1. `pd.read_csv` is great! See <http://pandas.pydata.org/pandas-docs/version/0.16.2/generated/pandas.read_csv.html> or of course, just use `pd.read_csv?`

### Steps

1. We can read the file directly from the URL. No need to downoad it seperately.
2. We do not need to unzip it first.
3. We must load it in chunks to keep the RAM memory load reasonable. 

In [2]:
import pandas as pd

print(pd.__version__)

1.0.2


In [2]:
# Practice with a very small file

#!wget http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Brewery.csv.gz

--2018-01-23 13:41:15--  http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Brewery.csv.gz
Resolving web.informatik.uni-mannheim.de... 134.155.95.98
Connecting to web.informatik.uni-mannheim.de|134.155.95.98|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 14744 (14K) [application/x-gzip]
Saving to: `Brewery.csv.gz.2'

100%[======================================>] 14,744      --.-K/s   in 0.01s   

2018-01-23 13:41:16 (982 KB/s) - `Brewery.csv.gz.2' saved [14744/14744]



In [3]:
!ls -lh Brewery.csv.gz

-rw-r--r--  1 admin  staff   100K Sep 24  2014 Brewery.csv.gz


In [4]:
#!gunzip Brewery.csv.gz
#!head Brewery.csv

# quick inspection without downloading everyuthing
!curl  http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Brewery.csv.gz|gunzip -c - |head -5

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 14744  100 14744    0     0  14744      0  0:00:01 --:--:--  0:00:01 61178
"URI","rdf-schema#label","foundedBy_label","foundedBy","foundingYear","industry_label","industry","internationally","keyPerson_label","keyPerson","location_label","location","locationCity_label","locationCity","locationCountry_label","locationCountry","owner_label","owner","parentCompany_label","parentCompany","product_label","product","revenue","type_label","type","point","22-rdf-syntax-ns#type_label","22-rdf-syntax-ns#type","rdf-schema#seeAlso_label","rdf-schema#seeAlso","owl#differentFrom_label","owl#differentFrom","wgs84_pos#lat","wgs84_pos#long"
"URI","http://www.w3.org/2000/01/rdf-schema#label","http://dbpedia.org/ontology/foundedBy","http://dbpedia.org/ontology/foundedBy","http://dbpedia.org/ontology/foundingYear","http://dbpedia.org/ontology/ind

In [6]:
url= 'http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Brewery.csv.gz'
# old http://web.informatik.uni-mannheim.de/DBpediaAsTables/csv/Brewery.csv.gz'

In [7]:
# standard way of reading in a csv file

df= pd.read_csv(url,
                encoding='utf8',
                compression='gzip', # which compression (infer does not work properly)
                sep=',',   # which seperator is used in the csv
                header=0,  # which line we want to use as the column names
                skiprows=[1,2,3],  # obvious
                index_col=0,   # which column we want for the index
                na_values='NULL' )  # Additional strings to recognize as NA/NaN. If dict passed, specific per-column NA valueshow to indicate null values

In [61]:
df.shape, len(df), len(df.columns)

((244, 33), 244, 33)

In [62]:
df.head()

rdf-schema#label  \
URI                                                                             
http://dbpedia.org/resource/5_Rabbit_Cervecería           5 Rabbit Cervecería   
http://dbpedia.org/resource/Abbey_Brewing_Company       Abbey Brewing Company   
http://dbpedia.org/resource/Ahlafors_Bryggerier           Ahlafors Bryggerier   
http://dbpedia.org/resource/AleSmith_Brewing_Co...   AleSmith Brewing Company   
http://dbpedia.org/resource/Alexander_Keith's_B...  Alexander Keith's Brewery   

                                                   foundedBy_label foundedBy  \
URI                                                                            
http://dbpedia.org/resource/5_Rabbit_Cervecería                NaN       NaN   
http://dbpedia.org/resource/Abbey_Brewing_Company              NaN       NaN   
http://dbpedia.org/resource/Ahlafors_Bryggerier                NaN       NaN   
http://dbpedia.org/resource/AleSmith_Brewing_Co...             NaN       NaN   
http://dbpedia.org/resource/Alexander_Keith's_B...             NaN       NaN   

                                                    foundingYear  \
URI                                                                
http://dbpedia.org/resource/5_Rabbit_Cervecería              NaN   
http://dbpedia.org/resource/Abbey_Brewing_Company            NaN   
http://dbpedia.org/resource/Ahlafors_Bryggerier              NaN   
http://dbpedia.org/resource/AleSmith_Brewing_Co...           NaN   
http://dbpedia.org/resource/Alexander_Keith's_B...           NaN   

                                                   industry_label industry  \
URI                                                                          
http://dbpedia.org/resource/5_Rabbit_Cervecería               NaN      NaN   
http://dbpedia.org/resource/Abbey_Brewing_Company             NaN      NaN   
http://dbpedia.org/resource/Ahlafors_Bryggerier               NaN      NaN   
http://dbpedia.org/resource/AleSmith_Brewing_Co...            NaN      NaN   
http://dbpedia.org/resource/Alexander_Keith's_B...            NaN      NaN   

                                                   internationally  \
URI                                                                  
http://dbpedia.org/resource/5_Rabbit_Cervecería                NaN   
http://dbpedia.org/resource/Abbey_Brewing_Company              NaN   
http://dbpedia.org/resource/Ahlafors_Bryggerier                NaN   
http://dbpedia.org/resource/AleSmith_Brewing_Co...             NaN   
http://dbpedia.org/resource/Alexander_Keith's_B...             NaN   

                                                   keyPerson_label keyPerson  \
URI                                                                            
http://dbpedia.org/resource/5_Rabbit_Cervecería                NaN       NaN   
http://dbpedia.org/resource/Abbey_Brewing_Company              NaN       NaN   
http://dbpedia.org/resource/Ahlafors_Bryggerier                NaN       NaN   
http://dbpedia.org/resource/AleSmith_Brewing_Co...             NaN       NaN   
http://dbpedia.org/resource/Alexander_Keith's_B...             NaN       NaN   

                                                                              location_label  \
URI                                                                                            
http://dbpedia.org/resource/5_Rabbit_Cervecería                        Bedford Park Illinois   
http://dbpedia.org/resource/Abbey_Brewing_Company                         Abiquiú New Mexico   
http://dbpedia.org/resource/Ahlafors_Bryggerier                    {Ale Municipality|Sweden}   
http://dbpedia.org/resource/AleSmith_Brewing_Co...      {California|San Diego|United States}   
http://dbpedia.org/resource/Alexander_Keith's_B...  {Halifax Nova Scotia|Canada|Nova Scotia}   

                                                        ...       type  \
URI                                                     ...              
http://dbpedia.org/resource/5_Rabbi

In [8]:
df['rdf-schema#label'].head(10)

URI
http://dbpedia.org/resource/5_Rabbit_Cervecería                5 Rabbit Cervecería
http://dbpedia.org/resource/Abbey_Brewing_Company            Abbey Brewing Company
http://dbpedia.org/resource/Ahlafors_Bryggerier                Ahlafors Bryggerier
http://dbpedia.org/resource/AleSmith_Brewing_Company      AleSmith Brewing Company
http://dbpedia.org/resource/Alexander_Keith's_Brewery    Alexander Keith's Brewery
http://dbpedia.org/resource/Alfa_Brewery                              Alfa Brewery
http://dbpedia.org/resource/Alpine_Beer_Company                Alpine Beer Company
http://dbpedia.org/resource/Amarcord_Brewery                      Amarcord Brewery
http://dbpedia.org/resource/Amber's_Brewing_Company        Amber's Brewing Company
http://dbpedia.org/resource/Andwells_Brewery                      Andwells Brewery
Name: rdf-schema#label, dtype: object

# Read the csv file in chunks

* And later concatenate them all

In [18]:
# See http://pandas.pydata.org/pandas-docs/stable/io.html#io-chunking

reader = pd.read_csv(url, 
                     sep=',', 
                     header=0, 
                     encoding='utf8',
                     compression='gzip',
                     skiprows=[1,2,3], 
                     index_col=0, 
                     na_values='NULL', 
                     #low_memory=False,
                     # usecols= withoutlabelcolumns, # the_columns_i_want_to_use, 
                     #
                     # New part: specify how many rows each chunk should have
                     #
                     chunksize=100)  



In [16]:
# Hoeveel chunks hebben we? We hadden 244 rows origineel.

chunks= [c for c in reader]
len(chunks), [len(c) for c in chunks]

(3, [100, 100, 44])

In [19]:
# Here I throw away those rows which have a NULL value on the location column
# Note that I have to run the reader definition again, if I run the previous cell.

%time df = pd.concat([ chunk.dropna(axis='index', subset=['location']) for chunk in reader ])
df.shape

CPU times: user 456 ms, sys: 1.34 s, total: 1.79 s
Wall time: 2.14 s


(184, 33)

# Now with a big file

In [20]:
#!wget http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Person.csv.gz
url='http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Band.csv.gz'

In [8]:
!ls -lh Band.csv.gz

-rw-r--r--  1 admin  staff    12M Sep 24  2014 Band.csv.gz


In [9]:
# quickly find out the columns

l = ! curl -s $url |gunzip -c  |head 

ef=l[0].split(',')  # take the first line of the file, and split on comma
print(ef)
#ef.index('"foundingYear"')  # now find the index of this column

['"URI"', '"rdf-schema#label"', '"foundedBy_label"', '"foundedBy"', '"foundingYear"', '"industry_label"', '"industry"', '"internationally"', '"keyPerson_label"', '"keyPerson"', '"location_label"', '"location"', '"locationCity_label"', '"locationCity"', '"locationCountry_label"', '"locationCountry"', '"owner_label"', '"owner"', '"parentCompany_label"', '"parentCompany"', '"product_label"', '"product"', '"revenue"', '"type_label"', '"type"', '"point"', '"22-rdf-syntax-ns#type_label"', '"22-rdf-syntax-ns#type"', '"rdf-schema#seeAlso_label"', '"rdf-schema#seeAlso"', '"owl#differentFrom_label"', '"owl#differentFrom"', '"wgs84_pos#lat"', '"wgs84_pos#long"']


In [10]:
# This may take a long time.
# Espeacially at home or on the train on slow internet
#It is more convenient with big files to download them outside pandas.
# At least you see what is going on.

#url= 'http://web.informatik.uni-mannheim.de/DBpediaAsTables/csv/Person.csv.gz'

reader = pd.read_csv('Band.csv.gz' , # url
                     sep=',', 
                     header=0, 
                     encoding='utf8',
                     compression='gzip',
                     skiprows=[1,2,3], 
                     index_col=0, 
                     na_values='NULL', 
                     low_memory=False,
                     # usecols= withoutlabelcolumns, # the_columns_i_want_to_use, 
                     #
                     # New part: specify how many rows each chunk should have
                     #
                     chunksize=10000) 

In [11]:
%time df = pd.concat([ chunk.dropna(axis='index', subset=['rdf-schema#label']) for chunk in reader ])
df.shape

CPU times: user 2.37 s, sys: 257 ms, total: 2.63 s
Wall time: 2.74 s


(30507, 87)

In [16]:
df.head()

rdf-schema#label  \
URI                                                                              
http://dbpedia.org/resource/With_Blood_Comes_Cl...  With Blood Comes Cleansing   
http://dbpedia.org/resource/With_One_Last_Breath          With One Last Breath   
http://dbpedia.org/resource/With_Passion                          With Passion   
http://dbpedia.org/resource/Withered                                  Withered   
http://dbpedia.org/resource/Within_Temptation                Within Temptation   

                                                                                   rdf-schema#comment  \
URI                                                                                                     
http://dbpedia.org/resource/With_Blood_Comes_Cl...  With Blood Comes Cleansing was an American Chr...   
http://dbpedia.org/resource/With_One_Last_Breath    With One Last Breath are a metalcore band from...   
http://dbpedia.org/resource/With_Passion            With Passion was an American technical death m...   
http://dbpedia.org/resource/Withered                Withered is an American extreme metal band fro...   
http://dbpedia.org/resource/Within_Temptation       Within Temptation is a Dutch symphonic metal/r...   

                                                    runtime  \
URI                                                           
http://dbpedia.org/resource/With_Blood_Comes_Cl...      NaN   
http://dbpedia.org/resource/With_One_Last_Breath        NaN   
http://dbpedia.org/resource/With_Passion                NaN   
http://dbpedia.org/resource/Withered                    NaN   
http://dbpedia.org/resource/Within_Temptation           NaN   

                                                           activeYearsEndYear  \
URI                                                                             
http://dbpedia.org/resource/With_Blood_Comes_Cl...  2010-01-01T00:00:00+02:00   
http://dbpedia.org/resource/With_One_Last_Breath                          NaN   
http://dbpedia.org/resource/With_Passion            2007-01-01T00:00:00+02:00   
http://dbpedia.org/resource/Withered                                      NaN   
http://dbpedia.org/resource/Within_Temptation                             NaN   

                                                         activeYearsStartYear  \
URI                                                                             
http://dbpedia.org/resource/With_Blood_Comes_Cl...  2005-01-01T00:00:00+02:00   
http://dbpedia.org/resource/With_One_Last_Breath    2008-01-01T00:00:00+02:00   
http://dbpedia.org/resource/With_Passion            2002-01-01T00:00:00+02:00   
http://dbpedia.org/resource/Withered                2003-01-01T00:00:00+02:00   
http://dbpedia.org/resource/Within_Temptation       1996-01-01T00:00:00+02:00   

                                                   alias artist_label artist  \
URI                                                                            
http://dbpedia.org/resource/With_Blood_Comes_Cl...   NaN          NaN    NaN   
http://dbpedia.org/resource/With_One_Last_Breath     NaN          NaN    NaN   
http://dbpedia.org/resource/With_Passion             NaN          NaN    NaN   
http://dbpedia.org/resource/Withered                 NaN          NaN    NaN   
http://dbpedia.org/resource/Within_Temptation        NaN          NaN    NaN   

                                                   associatedAct_label  \
URI                                                                      
http://dbpedia.org/resource/With_Blood_Comes_Cl...                 NaN   
http://dbpedia.org/resource/With_One_Last_Breath                   NaN   
http://dbpedia.org/resource/With_Passion                           NaN   
http://dbpedia.org/resource/Withered                               NaN   
http://dbpedia.org/resource/Within_Temptation                      NaN   

                                                   associatedAct  \
URI                      

In [19]:
# Save dataframe as pickle file. 

% time df.to_pickle('BANDDF')

# load back with df= df.read_pickle('BANDDF')

CPU times: user 901 ms, sys: 185 ms, total: 1.09 s
Wall time: 1.12 s


# Really big file

* .5 Gb zipped
* 4.5 Gb unzipped

## Techniques
* chunking
* select some columns in the reader
* select rows in the concatenation of the chunks

In [12]:
url= 'http://web.informatik.uni-mannheim.de/DBpediaAsTables/DBpedia-en-2016-04/csv/Person.csv.gz'

In [25]:
# quick inspection without downloading the file
!curl  $url |gunzip -c - |head -5

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0  186M    0  1192    0     0   1192      0 45:34:41 --:--:-- 45:34:41 12040"URI","rdf-schema#label","academicAdvisor_label","academicAdvisor","activeYears","activeYearsEndDate","activeYearsEndYear","activeYearsStartDate","activeYearsStartYear","address","agency_label","agency","alias","allegiance","almaMater_label","almaMater","appointer_label","appointer","artist_label","artist","associate_label","associate","associatedAct_label","associatedAct","associatedBand_label","associatedBand","associatedMusicalArtist_label","associatedMusicalArtist","author_label","author","automobileModel","award_label","award","background","battingSide","battle_label","battle","beatifiedBy_label","beatifiedBy","beatifiedDate","beatifiedPlace_label","beatifiedPlace","bestFinish","bibsysId","billed_label","billed","birthDate","birthName","birthPlace_l

### Inspect the file

* `gunzip -c` unzips to screen (stdout)
* we collect the first ten lines in a variable `l`


In [22]:
%%time

# what is the size compressed? How many words, lines characters are in it?
!ls -lh Person.csv.gz
! cat Person.csv.gz |gunzip -c  | wc

-rw-r--r--  1 admin  staff   187M Nov 14  2016 Person.csv.gz.1
 1517820 13467031 6281342206
CPU times: user 268 ms, sys: 98 ms, total: 366 ms
Wall time: 18.5 s


In [29]:
# inspect the names of the columns

l= !gunzip -c Person.csv.gz|head
ef=l[0].split(',')  # take the first line of the file, and split on comma

print(ef)
print("How many columns? ", len(ef))
print(ef.index('"birthDate"'))  # now find the index of this column

['"URI"', '"rdf-schema#label"', '"academicAdvisor_label"', '"academicAdvisor"', '"activeYears"', '"activeYearsEndDate"', '"activeYearsEndYear"', '"activeYearsStartDate"', '"activeYearsStartYear"', '"address"', '"agency_label"', '"agency"', '"alias"', '"allegiance"', '"almaMater_label"', '"almaMater"', '"appointer_label"', '"appointer"', '"artist_label"', '"artist"', '"associate_label"', '"associate"', '"associatedAct_label"', '"associatedAct"', '"associatedBand_label"', '"associatedBand"', '"associatedMusicalArtist_label"', '"associatedMusicalArtist"', '"author_label"', '"author"', '"automobileModel"', '"award_label"', '"award"', '"background"', '"battingSide"', '"battle_label"', '"battle"', '"beatifiedBy_label"', '"beatifiedBy"', '"beatifiedDate"', '"beatifiedPlace_label"', '"beatifiedPlace"', '"bestFinish"', '"bibsysId"', '"billed_label"', '"billed"', '"birthDate"', '"birthName"', '"birthPlace_label"', '"birthPlace"', '"birthYear"', '"block"', '"bnfId"', '"board_label"', '"board"', '

In [17]:
mycols=[0,1,2,52]  # Restrict the number of columns to only these

reader = pd.read_csv('Person.csv.gz',
                     sep=',', 
                     header=0, 
                     encoding='utf8',
                     compression='gzip',
                     skiprows=[1,2,3], 
                     index_col=0, 
                     na_values='NULL', 
                     low_memory=False,
                     usecols= mycols, # the_columns_i_want_to_use, 
                     #
                     # New part: specify how many rows each chunk should have
                     #
                     chunksize=10000) 

In [18]:
%%time
# Note that we now restrict the number of rows to those in which birthDate is not missing

df = pd.concat([ chunk.dropna(axis='index', subset=['birthDate']) for chunk in reader ])
print(df.shape)
df.head()

(969996, 3)
CPU times: user 1min 19s, sys: 16.9 s, total: 1min 36s
Wall time: 1min 36s


In [19]:
df.head()

rdf-schema#label  \
URI                                                                          
http://dbpedia.org/resource/Ingeborg_Moen_Borgerud  Ingeborg Moen Borgerud   
http://dbpedia.org/resource/Ingeborg_Nilsson              Ingeborg Nilsson   
http://dbpedia.org/resource/Ingeborg_Norell                Ingeborg Norell   
http://dbpedia.org/resource/Ingeborg_Pehrson              Ingeborg Pehrson   
http://dbpedia.org/resource/Ingeborg_Pf%C3%BCller         Ingeborg Pfüller   

                                                                                   rdf-schema#comment  \
URI                                                                                                     
http://dbpedia.org/resource/Ingeborg_Moen_Borgerud  Ingeborg Moen Borgerud (born 23 September 1949...   
http://dbpedia.org/resource/Ingeborg_Nilsson        Ingeborg Nilsson (1924 – 1995) was a Norwegian...   
http://dbpedia.org/resource/Ingeborg_Norell         Ingeborg Norell (born 1727) was the first Finn...   
http://dbpedia.org/resource/Ingeborg_Pehrson        Ingeborg Pehrson (16 December 1886 - 11 April ...   
http://dbpedia.org/resource/Ingeborg_Pf%C3%BCller   Ingeborg Ella Pfüller (born January 1 1932) wa...   

                                                                    birthDate  
URI                                                                            
http://dbpedia.org/resource/Ingeborg_Moen_Borgerud                 1949-09-23  
http://dbpedia.org/resource/Ingeborg_Nilsson        1924-01-01T00:00:00+02:00  
http://dbpedia.org/resource/Ingeborg_Norell         1727-01-01T00:00:00+02:00  
http://dbpedia.org/resource/Ingeborg_Pehrson                       1886-12-16  
http://dbpedia.org/resource/Ingeborg_Pf%C3%BCller                  1932-01-01

In [42]:
%time df.to_pickle('PersonDF.pkl.gz',compression='gzip') # takes to time compress
%ls -lh PersonDF.*

CPU times: user 33.7 s, sys: 829 ms, total: 34.6 s
Wall time: 35.3 s
-rw-r--r--  1 admin  staff   119M Mar  8 11:56 PersonDF.pkl.gz


In [26]:
%time new= pd.read_pickle('PersonDF.pkl.gz')
new.head()

CPU times: user 3.5 s, sys: 456 ms, total: 3.96 s
Wall time: 4.19 s


rdf-schema#label  \
URI                                                                          
http://dbpedia.org/resource/Ingeborg_Moen_Borgerud  Ingeborg Moen Borgerud   
http://dbpedia.org/resource/Ingeborg_Nilsson              Ingeborg Nilsson   
http://dbpedia.org/resource/Ingeborg_Norell                Ingeborg Norell   
http://dbpedia.org/resource/Ingeborg_Pehrson              Ingeborg Pehrson   
http://dbpedia.org/resource/Ingeborg_Pf%C3%BCller         Ingeborg Pfüller   

                                                                                   rdf-schema#comment  \
URI                                                                                                     
http://dbpedia.org/resource/Ingeborg_Moen_Borgerud  Ingeborg Moen Borgerud (born 23 September 1949...   
http://dbpedia.org/resource/Ingeborg_Nilsson        Ingeborg Nilsson (1924 – 1995) was a Norwegian...   
http://dbpedia.org/resource/Ingeborg_Norell         Ingeborg Norell (born 1727) was the first Finn...   
http://dbpedia.org/resource/Ingeborg_Pehrson        Ingeborg Pehrson (16 December 1886 - 11 April ...   
http://dbpedia.org/resource/Ingeborg_Pf%C3%BCller   Ingeborg Ella Pfüller (born January 1 1932) wa...   

                                                                    birthDate  
URI                                                                            
http://dbpedia.org/resource/Ingeborg_Moen_Borgerud                 1949-09-23  
http://dbpedia.org/resource/Ingeborg_Nilsson        1924-01-01T00:00:00+02:00  
http://dbpedia.org/resource/Ingeborg_Norell         1727-01-01T00:00:00+02:00  
http://dbpedia.org/resource/Ingeborg_Pehrson                       1886-12-16  
http://dbpedia.org/resource/Ingeborg_Pf%C3%BCller                  1932-01-01

# [Reading a gzipped file line by line](id:text)

In [ ]:
import gzip

with gzip.open('Brewery.csv.gz','r') as fin:
    c=0
    for line in fin:
        print 'Regel',c,':', line[100:150]
        c+=1

In [ ]:
!gunzip -c Brewery.csv.gz |head -1